## Final Project
## Winnie Lau

In [136]:
## Import necessary packages

%matplotlib osx 
import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [137]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2; # np.mod: return remainder of division
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

In [138]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.01 # m^2/yr

# uplift rate
uplift = 0.0

In [139]:
### Define simulation grid and initial conditions

NX = 30*2 #number of rows
NY = 30*2 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

In [140]:
### Model parameters

# Time step
dt = d**2 / D / 8.
#dt = d**2 / D / 16 #extra small steps 
#dt=100
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1.2

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10 

 dt[years] =  312.5


In [149]:
# Total simulation time
T = 1000.0 * 625.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of iteration: ',n_iter)

Number of iteration:  2000


In [150]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

## Simulation of a fault-crossing creek

In [151]:
### Define simulation grid and initial conditions

NX = 30*2 #number of rows
NY = 30*2 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

#initial condition 
Z = np.zeros((NX,NY))
xx = 0
yy = 0
h  = 5

for x in range (NX):
    xx += 0.1*NX
    h+=1
    for y in range (NY):
        yy += 0.1*NY
        h  += 1
    r  = 0.5*NX
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) 
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [152]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.2
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           0.0
Maximum elevation           58926.00219941231
Beach level                 11785.200439882463
Ocean volume                10269781.130157813
Percentage of ocean surface 35.0


In [153]:
%matplotlib osx 
# Set up figure

from matplotlib.animation import FFMpegWriter
metadata = dict(title='Fault-crossing landscape', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)

filename = "final_animation_new3.mp4"
fig = init_figure()
update_figure()
Znew = np.copy(Z)
with writer.saving(fig, filename, dpi=200):
    
    for it in range(1,200):
        if it %10 == 0:
            tmp = np.zeros((NX//2,NY))
            for x in range(NX//2):
                for y in range(NY):
                    tmp[x,y] = Z[x,(y+1)%NY] 

            for i in range(0,NX//2):
                for j in range(NY):  
                    Z[i,j] = tmp[i,j]

            tmp2 = np.zeros((NX-NX//2,NY))
            for x in range(NX-NX//2):
                for y in range(NY):
                    #print(x,y)
                    tmp2[x,y] = Z[x+NX//2,(y-1)%NY] 
            for i in range(NX//2,NX):
                for j in range(NY):  
                    Z[i,j] = tmp2[i-NX//2,j]
        

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # 
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: 
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                #if (CFL>1.0):
                    #print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0.       

        writer.grab_frame()
        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,5)==0): 
            print(it,end='')
            update_figure()
            print('Max Elevation=',np.max(Z), 'Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure()
    print(' Simulation finished.')

....5Max Elevation= 58667.86445411128 Ocean level= 11783.39005891587  Ocean surface fraction= 36.111111111111114
....10Max Elevation= 58400.88875004727 Ocean level= 11771.969764077512  Ocean surface fraction= 36.638888888888886
....15Max Elevation= 58125.70530420336 Ocean level= 11770.325852533644  Ocean surface fraction= 37.166666666666664
....20Max Elevation= 57841.6332520988 Ocean level= 11765.090042761229  Ocean surface fraction= 37.5
....25Max Elevation= 57548.75432242526 Ocean level= 11760.742855325929  Ocean surface fraction= 38.361111111111114
....30Max Elevation= 57246.27178416539 Ocean level= 11758.019457414135  Ocean surface fraction= 38.47222222222222
....35Max Elevation= 56934.27110583563 Ocean level= 11753.668122681791  Ocean surface fraction= 39.30555555555556
....40Max Elevation= 56611.92398156716 Ocean level= 11753.668122681791  Ocean surface fraction= 39.47222222222222
....45Max Elevation= 56279.339747740596 Ocean level= 11752.423900802407  Ocean surface fraction= 40.

## Simulation of the erosion without fault

In [146]:
### Define simulation grid and initial conditions

NX = 30*2 #number of rows
NY = 30*2 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

#initial condition 
Z = np.zeros((NX,NY))
xx = 0
yy = 0
h  = 5

for x in range (NX):
    xx += 0.1*NX
    h+=1
    for y in range (NY):
        yy += 0.1*NY
        h  += 1
    r  = 0.5*NX
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) 
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [147]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.2
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           0.0
Maximum elevation           58926.00219941231
Beach level                 11785.200439882463
Ocean volume                10269781.130157813
Percentage of ocean surface 35.0


In [148]:
%matplotlib osx 
# Set up figure

from matplotlib.animation import FFMpegWriter
metadata = dict(title='Erosion without fault', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)

filename = "final_animation_org3.mp4"
fig = init_figure()
update_figure()
Znew = np.copy(Z)
with writer.saving(fig, filename, dpi=200):
    
    for it in range(1,200):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx 
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: 
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                #if (CFL>1.0):
                    #print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        writer.grab_frame()
        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,5)==0): 
            print(it,end='')
            update_figure()
            print(' Max Elevation=',np.max(Z),' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

    update_figure()
    print(' Simulation finished.')

....5 Max Elevation= 58667.86445411128  Ocean level= 11783.39005891587  Ocean surface fraction= 36.111111111111114
....10 Max Elevation= 58400.88875004727  Ocean level= 11783.39005891587  Ocean surface fraction= 36.666666666666664
....15 Max Elevation= 58125.40897276477  Ocean level= 11783.39005891587  Ocean surface fraction= 37.05555555555556
....20 Max Elevation= 57841.17211717147  Ocean level= 11780.926094585357  Ocean surface fraction= 37.44444444444444
....25 Max Elevation= 57547.84567836258  Ocean level= 11780.926094585357  Ocean surface fraction= 37.97222222222222
....30 Max Elevation= 57245.07378893808  Ocean level= 11780.926094585357  Ocean surface fraction= 38.30555555555556
....35 Max Elevation= 56932.49637088385  Ocean level= 11779.833370774042  Ocean surface fraction= 38.55555555555556
....40 Max Elevation= 56609.75639186483  Ocean level= 11779.833370774042  Ocean surface fraction= 38.77777777777778
....45 Max Elevation= 56276.50207706943  Ocean level= 11779.833370774042  